In [53]:
import warnings
warnings.filterwarnings('ignore')
warnings.filterwarnings(action='once')

In [2]:
import pandas as pd
import numpy as np

from pathlib import Path
from rdkit import Chem
from rdkit.Chem import Descriptors

In [73]:
tox21 = Path("../data/tox21/downsampled")
train = pd.read_csv(tox21 / "train.csv")
eval = pd.read_csv(tox21 / "eval.csv")
test = pd.read_csv(tox21 / "test.csv")

In [4]:
def split_by_features(df):
    X = df[["smiles"]]
    try:
        y = df[["NR-AR", "NR-AR-LBD", "NR-AhR", "NR-Aromatase", "NR-ER", "NR-ER-LBD", "NR-PPAR-gamma", "SR-ARE", "SR-ATAD5", "SR-HSE", "SR-MMP", "SR-p53"]]
    except:
        y = df[["FDA_APPROVED"]]
    return X, y

In [61]:
from sklearn.preprocessing import StandardScaler
from sklearn.pipeline import Pipeline
from sklearn.feature_selection import VarianceThreshold
from sklearn.multioutput import MultiOutputClassifier
from sklearn.linear_model import LogisticRegression
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import hamming_loss, f1_score
from sklearn.decomposition import PCA



class ChemFeatureGenerator():
    def fit(self, X, y = None):
        self.droped = None
        return self
    
    def _getMolDescriptors(self, mol, missingVal=None):
        ''' calculate the full list of descriptors for a molecule
        
            missingVal is used if the descriptor cannot be calculated
        '''
        res = {}
        for nm,fn in Descriptors._descList:
            # some of the descriptor fucntions can throw errors if they fail, catch those here:
            try:
                val = fn(mol)
            except:
                # print the error message:
                import traceback
                traceback.print_exc()
                # and set the descriptor value to whatever missingVal is
                val = missingVal
            res[nm] = val
        return res
    
    def transform(self, X):
        df = X[["smiles"]].apply(lambda x: Chem.MolFromSmiles(x[0]), axis=1)
        res = df.apply(lambda x: self._getMolDescriptors(x)).values.tolist()
        X = pd.DataFrame(res)
        if self.droped == None:
            self.droped = X.columns[X.isna().any()].tolist()
            X = X.dropna(axis=1)
            
        X = X.drop(columns=self.droped)
        return X
    


### Logistic regression model

In [66]:
X, y = split_by_features(train)
pca = PCA()

pipeLogistic = Pipeline([
    ('feature_generator', ChemFeatureGenerator()),
    ('scaller', StandardScaler()),
    ('pca', pca),
    ('logistic', MultiOutputClassifier(LogisticRegression())),
])

from sklearn.model_selection import GridSearchCV
logistic_param_grid = {
    "pca__n_components": [5, 15, 30, 45, 60],
}
search_lr = GridSearchCV(pipeLogistic, logistic_param_grid, n_jobs=2)
search_lr.fit(X, y)


print("Best parameter (CV score=%0.3f):" % search_lr.best_score_)
print(search_lr.best_params_)


/tmp/ipykernel_17644/3509895422.py:36: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
/tmp/ipykernel_17644/3509895422.py:36: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
[17:29:01] DEPRECATION WARNING: please use MorganGenerator
[17:29:01] DEPRECATION WARNING: please use MorganGenerator
[17:29:01] DEPRECATION WARNING: please use MorganGenerator
[17:29:01] DEPRECATION WARNING: please use MorganGenerator
[17:29:01] DEPRECATION WARNING: please use MorganGenerator
[17:29:01] DEPRECATION WARNING: please use MorganGenerator
[17:29:01] DEPRECATION WARNING: please use MorganGenerator
[17:29:01] DEPRECATION WARNING: please use Mo

Best parameter (CV score=nan):
{'pca__n_components': 5}


### RF Model

In [65]:
X, y = split_by_features(train)
pca = PCA()

pipeRandomForest = Pipeline([
    ('feature_generator', ChemFeatureGenerator()),
    ('scaller', StandardScaler()),
    ('pca', pca),
    ('model', MultiOutputClassifier(RandomForestClassifier()))
])


rf_param_grid = {
    "pca__n_components": [5, 15, 30, 45, 60],
}
search_rf = GridSearchCV(pipeRandomForest, rf_param_grid, n_jobs=2)
search_rf.fit(X, y)


print("Best parameter (CV score=%0.3f):" % search_rf.best_score_)
print(search_rf.best_params_)

/tmp/ipykernel_17644/3509895422.py:36: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
/tmp/ipykernel_17644/3509895422.py:36: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
[17:27:45] DEPRECATION WARNING: please use MorganGenerator
[17:27:45] DEPRECATION WARNING: please use MorganGenerator
[17:27:45] DEPRECATION WARNING: please use MorganGenerator
[17:27:45] DEPRECATION WARNING: please use MorganGenerator
[17:27:45] DEPRECATION WARNING: please use MorganGenerator
[17:27:45] DEPRECATION WARNING: please use MorganGenerator
[17:27:45] DEPRECATION WARNING: please use MorganGenerator
[17:27:45] DEPRECATION WARNING: please use Mo

Best parameter (CV score=nan):
{'pca__n_components': 5}


In [76]:
datasets = (("train", train), ("eval", eval), ("test",test))
models = (("rf", search_rf), ("lr", search_lr))
res = {
    "dataset": [],
    "model": [],
    "hamming": [],
    "samples": [],
    "micro": [],
    "macro": []
}

for d_name, dataset in datasets:
    for m_name, model in models:
        X, y = split_by_features(dataset)
        y_predict = model.predict(X)
        hamming = hamming_loss(y_predict,y)
        f1_samples = f1_score(y_predict, y, average="samples")
        f1_micro = f1_score(y_predict, y, average="micro")
        f1_macro = f1_score(y_predict, y, average="macro")
        res["dataset"].append(d_name)
        res["model"].append(m_name)
        res["hamming"].append(hamming)
        res["samples"].append(f1_samples)
        res["micro"].append(f1_micro)
        res["macro"].append(f1_macro)


/tmp/ipykernel_17644/3509895422.py:36: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  df = X[["smiles"]].apply(lambda x: Chem.MolFromSmiles(x[0]), axis=1)
[17:40:18] DEPRECATION WARNING: please use MorganGenerator
[17:40:18] DEPRECATION WARNING: please use MorganGenerator
[17:40:18] DEPRECATION WARNING: please use MorganGenerator
[17:40:18] DEPRECATION WARNING: please use MorganGenerator
[17:40:18] DEPRECATION WARNING: please use MorganGenerator
[17:40:18] DEPRECATION WARNING: please use MorganGenerator
[17:40:18] DEPRECATION WARNING: please use MorganGenerator
[17:40:18] DEPRECATION WARNING: please use MorganGenerator
[17:40:18] DEPRECATION WARNING: please use MorganGenerator
[17:40:18] DEPRECATION WARNING: please use MorganGenerator
[17:40:18] DEPRECATION WARNING: please use MorganGenerator
[17:40:18

In [77]:
pd.DataFrame(res)

dataset model   hamming   samples     micro     macro
0   train    rf  0.000912  0.912264  0.996097  0.995668
1   train    lr  0.112874  0.037026  0.129395  0.121318
2    eval    rf  0.119391  0.177106  0.280193  0.224806
3    eval    lr  0.124199  0.025855  0.093567  0.117749
4    test    rf  0.118836  0.193815  0.271903  0.174794
5    test    lr  0.120809  0.015680  0.046693  0.049250

### Clintox

In [79]:
clintox = Path("../data/clintox/downsampled")
train = pd.read_csv(clintox / "train.csv")
eval = pd.read_csv(clintox / "eval.csv")
test = pd.read_csv(clintox / "test.csv")


In [80]:
X, y = split_by_features(train)
pca = PCA()

pipeLogistic = Pipeline([
    ('feature_generator', ChemFeatureGenerator()),
    ('scaller', StandardScaler()),
    ('pca', pca),
    ('logistic', MultiOutputClassifier(LogisticRegression())),
])

from sklearn.model_selection import GridSearchCV
logistic_param_grid = {
    "pca__n_components": [5, 15, 30, 45, 60],
}
search_lr = GridSearchCV(pipeLogistic, logistic_param_grid, n_jobs=2)
search_lr.fit(X, y)


print("Best parameter (CV score=%0.3f):" % search_lr.best_score_)
print(search_lr.best_params_)

/home/tibor/Documents/msc-datascience/2024w/Toxic/ToxicML/.venv/lib/python3.12/site-packages/joblib/externals/loky/backend/fork_exec.py:38: DeprecationWarning: This process (pid=17644) is multi-threaded, use of fork() may lead to deadlocks in the child.
  pid = os.fork()
/tmp/ipykernel_17644/3509895422.py:36: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
/tmp/ipykernel_17644/3509895422.py:36: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
[17:43:37] DEPRECATION WARNING: please use MorganGenerator
[17:43:37] DEPRECATION WARNING: please use MorganGenerator
[17:43:37] DEPRECATION WARNING: please use MorganGenerator
[17:43:37

Best parameter (CV score=nan):
{'pca__n_components': 5}


[17:43:55] DEPRECATION WARNING: please use MorganGenerator
[17:43:55] DEPRECATION WARNING: please use MorganGenerator
[17:43:55] DEPRECATION WARNING: please use MorganGenerator
[17:43:55] DEPRECATION WARNING: please use MorganGenerator
[17:43:55] DEPRECATION WARNING: please use MorganGenerator
[17:43:55] DEPRECATION WARNING: please use MorganGenerator
[17:43:55] DEPRECATION WARNING: please use MorganGenerator
[17:43:55] DEPRECATION WARNING: please use MorganGenerator
[17:43:55] DEPRECATION WARNING: please use MorganGenerator
[17:43:55] DEPRECATION WARNING: please use MorganGenerator
[17:43:55] DEPRECATION WARNING: please use MorganGenerator
[17:43:55] DEPRECATION WARNING: please use MorganGenerator
[17:43:55] DEPRECATION WARNING: please use MorganGenerator
[17:43:55] DEPRECATION WARNING: please use MorganGenerator
[17:43:55] DEPRECATION WARNING: please use MorganGenerator
[17:43:55] DEPRECATION WARNING: please use MorganGenerator
[17:43:55] DEPRECATION WARNING: please use MorganGenerat

In [81]:
X, y = split_by_features(train)
pca = PCA()

pipeRandomForest = Pipeline([
    ('feature_generator', ChemFeatureGenerator()),
    ('scaller', StandardScaler()),
    ('pca', pca),
    ('model', MultiOutputClassifier(RandomForestClassifier()))
])


rf_param_grid = {
    "pca__n_components": [5, 15, 30, 45, 60],
}
search_rf = GridSearchCV(pipeRandomForest, rf_param_grid, n_jobs=2)
search_rf.fit(X, y)


print("Best parameter (CV score=%0.3f):" % search_rf.best_score_)
print(search_rf.best_params_)

/tmp/ipykernel_17644/3509895422.py:36: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
/tmp/ipykernel_17644/3509895422.py:36: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
[17:44:33] DEPRECATION WARNING: please use MorganGenerator
[17:44:33] DEPRECATION WARNING: please use MorganGenerator
[17:44:33] DEPRECATION WARNING: please use MorganGenerator
[17:44:33] DEPRECATION WARNING: please use MorganGenerator
[17:44:33] DEPRECATION WARNING: please use MorganGenerator
[17:44:33] DEPRECATION WARNING: please use MorganGenerator
[17:44:33] DEPRECATION WARNING: please use MorganGenerator
[17:44:33] DEPRECATION WARNING: please use Mo

Best parameter (CV score=nan):
{'pca__n_components': 5}


In [97]:
datasets = (("train", train), ("eval", eval), ("test",test))
models = (("rf", search_rf), ("lr", search_lr))
res = {
    "dataset": [],
    "model": [],
    "f1": [],
}

for d_name, dataset in datasets:
    for m_name, model in models:
        X, y = split_by_features(dataset)
        y_predict = model.predict(X)
        f1 = f1_score(y_predict, y)
        res["dataset"].append(d_name)
        res["model"].append(m_name)
        res["f1"].append(f1)


/tmp/ipykernel_17644/3509895422.py:36: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  df = X[["smiles"]].apply(lambda x: Chem.MolFromSmiles(x[0]), axis=1)
[17:47:54] DEPRECATION WARNING: please use MorganGenerator
[17:47:54] DEPRECATION WARNING: please use MorganGenerator
[17:47:54] DEPRECATION WARNING: please use MorganGenerator
[17:47:54] DEPRECATION WARNING: please use MorganGenerator
[17:47:54] DEPRECATION WARNING: please use MorganGenerator
[17:47:54] DEPRECATION WARNING: please use MorganGenerator
[17:47:54] DEPRECATION WARNING: please use MorganGenerator
[17:47:54] DEPRECATION WARNING: please use MorganGenerator
[17:47:54] DEPRECATION WARNING: please use MorganGenerator
[17:47:55] DEPRECATION WARNING: please use MorganGenerator
[17:47:55] DEPRECATION WARNING: please use MorganGenerator
[17:47:55

ValueError: The feature names should match those that were passed during fit.
Feature names unseen at fit time:
- BCUT2D_CHGHI
- BCUT2D_CHGLO
- BCUT2D_LOGPHI
- BCUT2D_LOGPLOW
- BCUT2D_MRHI
- ...


'eval'